# Random Forest Baseline

Cloned from: [Feature_selection_LR_airlinejoin (baseline-3)](tobe update)
- Has the hyperparameter tuning for the baseline with all features for midterm.

- What is this notebook for? 
  - Notebook that runs the baseline Random Forest model of the project on the top features selected by Random Forest's Feature Importance
  - Machine Learning Algorithms : Random Forest
  - Metrics: F1, accuracy, precision
  
---
  
- Data:
  - Final, cleaned weather
  - Cleaned flights minus (PR departure delay, PR arrival delay, carrier ordinal)

RF in spark

https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/1898361324232092/command/1898361324232093

Feature selection in RF

https://antonhaugen.medium.com/feature-selection-for-pyspark-tree-classifiers-3be54a8bc493

# 0. Preparation

In [0]:
import pandas as pd
import numpy as np
import os
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import ast
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import geopandas as gpd
import folium
import time

from pyspark.sql.functions import col, max, min
from pyspark.sql.functions import col,isnan,when,count
from pyspark.sql.functions import desc
from pyspark.sql.types import DateType
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler
from pyspark.ml.feature import MinMaxScaler
from pyspark.mllib.evaluation import MulticlassMetrics, BinaryClassificationMetrics
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.sql.functions import add_months, date_add
from pyspark.ml.classification import RandomForestClassifier

from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta

In [0]:
# Put at the top of any notebooks for storing in blob

from pyspark.sql.functions import col, max

blob_container = "team06" # The name of your container created in https://portal.azure.com
storage_account = "apatel" # The name of your Storage account created in https://portal.azure.com
secret_scope = "team06" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "team06" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

## Import fully joined data

In [0]:
df_5yr_join = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_depPR_arrPR_v3')

In [0]:
# copied from section `Flights Features to Keep`
features_for_flights=[ 'DISTANCE','ORI_elevation','DEST_elevation', 
                   'prior_dep_delayed', 'previous_DEP_DELAY_NEW',
                    'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here',
                    'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs',
                    'daytime', 'evening',
                    'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands',
                    'summer', 'winter', 'autumn',
                    'weekend_or_holiday']
# one-hot encoded variables should be n-1. Eliminate one of the one-hot encoded categoricals to the all 0 case represents it.
# Dropped: 'late_night', 'new_england', 'spring'


features_for_weathers=['OC1_0_wind_gust_spd_rate_imp','AA1_1_liquid_precip','AA3_1_liquid_precip','gd1_0_sky_coverage',
                       'au2_4_extreme_wind_weather','mv1_0_sand_dust_near','mv1_0_thunder_rain_near','aw1_mw1_0_smoke_haze_dust','aw1_mw1_0_fog',
                       'aw1_mw1_0_rain_drizzle','aw1_mw1_0_freezing_rain_drizzle','aw1_mw1_0_snow','aw1_mw1_0_hail_or_ice','aw1_mw1_0_thunderstorm',
                       'aw1_mw1_0_tornado','SLP_0_avg_station_press_imp','WND_3_wind_speed_imp','CIG_0_sky_ceiling_height_imp',
                       'VIS_0_visibility_dist_imp','TMP_0_air_temperature_imp','DEW_0_dew_pt_temp_imp','MA1_0_altimeter_set_rate_imp',
                       'MA1_2_station_pres_rate_imp','GD1_3_cloud_height_imp']

features_for_pagerank = ['depDelayPageRank', 'arrDelayPageRank']

# Original total features
feature_list_full_0 = features_for_flights + features_for_weathers + features_for_pagerank


feature_list_full = ['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado'] + ['depDelayPageRank', 'arrDelayPageRank']


feature_list = ['prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'evening', 'previous_ARR_DELAY_NEW', 
                'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs',
               'depDelayPageRank', 'arrDelayPageRank']


# specify any outcome variables you also want to check for missing
outcomes_for_flights=['DEP_DEL15']#, 'DEP_DELAY_NEW']

# combine:
model_col_list = outcomes_for_flights + feature_list_full_0

print(model_col_list)

['DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
features_for_cv = ['DATE'] + outcomes_for_flights + feature_list_full_0
print(features_for_cv)

['DATE', 'DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
display(df_5yr_join)
print(df_5yr_join.count())

YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 CANCELLED ACTUAL_ELAPSED_TIME DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY LATE_AIRCRAFT_DELAY ORI_IATA ORI_station_id ORI_station_lat ORI_station_lon ORI_airport_lat ORI_airport_lon ORI_elevation ORI_dist_airp_sta DEST_IATA DEST_station_id DEST_station_lat DEST_station_lon DEST_airport_lat DEST_airport_lon DEST_elevation DEST_dist_airp_sta CRS_DEP_HRS CRS_DEP_MINS CRS_DEP_TIME_STR CRS_DEP_DT_STR CRS_DEP_DATETIME iata_code ORI_timezone CRS_DEP_DATETIME_UTC CRS_DEP_DATETIME_UTC_END CRS_DEP_DATETIME_UTC_START STATION DATE LATITUDE LONGITUDE ELEVATION REPORT_TYPE DEST_timezone DEP_HRS DEP_MINS DEP_TIME_STR DEP_DT_STR DEP_DATETIME ARR_DATETIME_ACTUAL_UTC late_night daytime evening region_name new_england mid_atlantic south midwest southwest west pacific_islands atlantic_islands spring summer autumn winter dep_date weekend_or_holiday flightID ID previous_flight_delay_status previous_flight_dep_time time_between_departures_min valid_dep_delay prior_dep_delayed previous_DEP_DELAY_NEW_value previous_DEP_DELAY_NEW previous_flight_arrdelay_status previous_flight_arr_time time_between_arrival_and_end_min valid_arr_delay prior_arr_delayed previous_ARR_DELAY_NEW_value previous_ARR_DELAY_NEW prev_arrival_airport plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs year_quarter quarter_enum quarter_enum_prev month_seq_index wnd_2_wind_obs_type wnd_3_wind_sp_rate cig_0_height vis_0_distance slp_0_day_avg tmp_0_air_temp dew_0_point_temp ma1_0_altimeter_setting_rate ma1_2_station_pressure_rate gd1_3_sky_cover_height WND_3_wind_speed CIG_0_sky_ceiling_height VIS_0_visibility_dist SLP_0_avg_station_press TMP_0_air_temperature DEW_0_dew_pt_temp MA1_0_altimeter_set_rate MA1_2_station_pres_rate OC1_0_wind_gust_spd_rate_imp GD1_3_cloud_height AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank 2015 1 1 1 4 2015-01-01 B6 20409 N324JB 2023 12478 1247802 JFK NY 36 New York 14843 1484304 SJU PR 72 Puerto Rico 535 618 43.0 43.0 1.0 2 0001-0559 1020 1039 19.0 19.0 1.0 0.0 201.0 1598.0 7 19.0 0.0 0.0 0.0 JFK 74486094789 40.639 -73.762 40.63980103 -73.77890015 13.0 1.4287707081898418 null null null null null null 841.0 null 5 35 05:35 2015-01-01 05:35 2015-01-01T05:35:00.000+0000 JFK America/New_York 2015-01-01T10:35:00.000+0000 2015-01-01T08:35:00.000+0000 2015-01-01T06:35:00.000+0000 74486094789 2015-01-01T07:51:00.000+0000 40.6386 -73.7622 3.4 FM-15 America/Puerto_Rico 06 18 06:18 2015-01-01 06:18 2015-01-01T06:18:00.000+0000 2015-01-01T14:39:00.000+0000 1 0 0 mid_atlantic 0 1 0 0 0 0 0 0 0 0 0 1 2015-01-01 1 180388780851 B6N324JBJFK2015-01-01535 null null null no 0 null 0.0 null null null no 0 null 0.0 LGA 0 0.12 274 83 0.13 2015-1 0 -1 1 N 0062 22000 016093 10212 -0017 -0117 10213 10205 +04267 62 22000 16093 10212 -17 -117 10213 10205 0 4267 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015 1 3 28 6 2015-03-28 B6 20409 N316JB 2323 11278 1127802 D

31080934

In [0]:
# null check
def displayMissingInDF(flights_df, cols_to_check = None):
  # train0_null_check = train0.drop("CRS_DEP_DATETIME_UTC_END")
  if type(cols_to_check)==list:
    pass
  else:
    cols_to_check = flights_df.columns
  null_cnt_df = flights_df.select([count(when(col(c).contains('None') | \
                            col(c).contains('NULL') | \
                            (col(c) == '' ) | \
                            col(c).isNull() | \
                            isnan(c), c 
                           )).alias(c)
                    for c in cols_to_check])

  display(null_cnt_df)

## Select features for CV split and modeling

In [0]:
df_5yr_join_cv = df_5yr_join.select(features_for_cv)

In [0]:
displayMissingInDF(df_5yr_join_cv, model_col_list)

DEP_DEL15 DISTANCE ORI_elevation DEST_elevation prior_dep_delayed previous_DEP_DELAY_NEW prior_arr_delayed previous_ARR_DELAY_NEW plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs daytime evening mid_atlantic south midwest southwest west pacific_islands atlantic_islands summer winter autumn weekend_or_holiday OC1_0_wind_gust_spd_rate_imp AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [0]:
display(df_5yr_join_cv)

DATE DEP_DEL15 DISTANCE ORI_elevation DEST_elevation prior_dep_delayed previous_DEP_DELAY_NEW prior_arr_delayed previous_ARR_DELAY_NEW plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs daytime evening mid_atlantic south midwest southwest west pacific_islands atlantic_islands summer winter autumn weekend_or_holiday OC1_0_wind_gust_spd_rate_imp AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank 2015-01-01T07:51:00.000+0000 1.0 1598.0 13.0 841.0 0 0.0 0 0.0 0 0.12 274 83 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 759.0 15.0 96.0 0 0.0 0 0.0 0 0.27 178 391 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 1547.0 1026.0 841.0 0 0.0 0 0.0 1 0.17 997 63 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 842.0 26.0 146.0 0 6.0 0 0.0 0 0.25 173 187 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T07:51:00.000+0000 1.0 1089.0 13.0 8.0 0 0.0 0 0.0 0 0.17 274 208 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 547.0 15.0 1026.0 0 0.0 0 0.0 0 0.26 178 912 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 1747.0 1026.0 2181.0 1 24.0 1 16.0 1 0.17 997 373 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 507.0 26.0 748.0 0 0.0 0 0.0 0 0.23 173 243 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T07:51:00.000+0000 0.0 1576.0 13.0 841.0 0 0.0 0 0.0 0 0.12 274 6 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 1184.0 15.0 487.0 0 5.0 0 0.0 0 0.26 178 116 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 332.0 1026.0 341.0 0 0.0 0 0.0 0 0.17 997 43 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 406.0 26.0 1026.0 0 0.0 0 0.0 0 0.14 173 678 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T09:00:00.000+0000 0.0 944.0 13.0 96.0 0 0.0 0 0.0 0 0.12 274 303 0.13 1 0 1 0 0 0 0 0 0 

In [0]:
df_5yr_join_cv = df_5yr_join_cv.cache()
print(f"Number of rows in dataset pre-split: {df_5yr_join_cv.count()}")

Number of rows in dataset pre-split: 31080934

# 2. Train/ Hold-out/ Test split

- As a preparation for cross validation, dataset is splitted by time
- Hold-out data always comes later than train data and test data comes later than all the train/ hold-out data

## Conduct Block Time Series Split (5 years)
CV diagram for the entire dataset:

![CV for Full Data](files/shared_uploads/anand.patel@berkeley.edu/CV_full_data.PNG)

## Conduct Block Time Series Split (5 years)
CV diagram for the entire dataset:

![CV for Full Data](files/shared_uploads/anand.patel@berkeley.edu/CV_full_data.PNG)

|      | Train                    | Hold-out                 | Test                |
|------|--------------------------|--------------------------|---------------------|
| 1    | 2015-01-01 to 2015-06-30 | 2015-07-01 to 2015-08-31 | -                   |
| 2    | 2015-06-01 to 2015-11-30 | 2015-12-01 to 2016-01-31 | -                   |
| 3    | 2015-11-01 to 2016-04-30 | 2016-05-01 to 2016-06-30 | -                   |
| 4    | 2016-04-01 to 2016-09-30 | 2016-10-01 to 2016-11-30 | -                   |
| 5    | 2016-09-01 to 2017-02-28 | 2017-03-01 to 2016-04-30 | -                   |
| 6    | 2017-02-01 to 2017-07-31 | 2017-08-01 to 2017-09-30 | -                   |
| 7    | 2017-07-01 to 2018-12-31 | 2017-02-01 to 2017-02-28 | -                   |
| 8    | 2017-12-01 to 2018-05-30 | 2018-06-01 to 2018-07-31 | -                   |
| 9    | 2018-05-01 to 2018-10-31 | 2018-11-01 to 2018-12-31 |                     |
| Test | -                        | -                        | 2019-01-01 to end   |

In [0]:
# save out the data with just these columns.
# df_5yr_join_cv.write.parquet(f"{blob_url}/flights_all_feats_and_imputed_weather_v4_29")

In [0]:
# df_5yr_join_cv = spark.read.parquet(f'{blob_url}/flights_all_feats_and_imputed_weather_v4_29')
# display(df_5yr_join_cv)

In [0]:
print(features_for_cv)

['DATE', 'DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
# Data split for 5-year CV is calcutated by the latest date

# name latest record as "latest_record"
df_CV_date = df_5yr_join_cv.select(max("DATE")).withColumnRenamed("max(DATE)","latest_record")
# name the start date of test data as test_start

df_CV_date = df_CV_date.withColumn("test_start_", add_months("latest_record",-12))
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("test_start", date_add("test_start_",+1))


# start date of cv group1: train0
df_CV_date = df_CV_date.withColumn("train0_", add_months("latest_record",-60)).cache()
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("train0", date_add("train0_",+1))


# same as group1, calculate group2 to 8
df_CV_date = df_CV_date.withColumn("train1", add_months("train0",+5))
df_CV_date = df_CV_date.withColumn("train2", add_months("train0",+10))
df_CV_date = df_CV_date.withColumn("train3", add_months("train0",+15))
df_CV_date = df_CV_date.withColumn("train4", add_months("train0",+20))
df_CV_date = df_CV_date.withColumn("train5", add_months("train0",+25))
df_CV_date = df_CV_date.withColumn("train6", add_months("train0",+30))
df_CV_date = df_CV_date.withColumn("train7", add_months("train0",+35))
df_CV_date = df_CV_date.withColumn("train8", add_months("train0",+40))

# start date of cv group1: holdout0
df_CV_date = df_CV_date.withColumn("holdout0", add_months("train0",+6))
df_CV_date = df_CV_date.withColumn("holdout1", add_months("holdout0",+5))
df_CV_date = df_CV_date.withColumn("holdout2", add_months("holdout0",+10))
df_CV_date = df_CV_date.withColumn("holdout3", add_months("holdout0",+15))
df_CV_date = df_CV_date.withColumn("holdout4", add_months("holdout0",+20))
df_CV_date = df_CV_date.withColumn("holdout5", add_months("holdout0",+25))
df_CV_date = df_CV_date.withColumn("holdout6", add_months("holdout0",+30))
df_CV_date = df_CV_date.withColumn("holdout7", add_months("holdout0",+35))
df_CV_date = df_CV_date.withColumn("holdout8", add_months("holdout0",+40))

display(df_CV_date)

# use pandas because operation is much lighter
pdf_CV_date = df_CV_date.cache().toPandas()
print(pdf_CV_date)

# list of name of the dataset
cv_group_list = [['train0','holdout0'],['train1','holdout1'],['train2','holdout2'],
                 ['train3','holdout3'],['train4','holdout4'],['train5','holdout5'],
                 ['train6','holdout6'],['train7','holdout7'],['train8','holdout8']]


def CVSplit_full1(df, cv_group, feature_list):
  
  global pdf_CV_date#df_CV_date
  
  # assign start date
  train_start_date = pdf_CV_date[cv_group[0]][0]
  holdout_start_date = pdf_CV_date[cv_group[1]][0]
  print(f'{cv_group[0]}_start: {train_start_date}, {cv_group[1]}_start: {holdout_start_date}')

  # calculate end date of train/holdout data
  pdf_CV_date[cv_group[0]+'_end'] = train_start_date + relativedelta(months=+5)
  pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+2)
  
  # calculate end date of train/holdout data
  train_end_date = train_start_date + relativedelta(months=+6) - timedelta(days=1)
  holdout_end_date = holdout_start_date + relativedelta(months=+2) - timedelta(days=1)
  print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
    
  # train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= train_start_date) & (df_5yr_join_cv.DATE <= train_end_date))
  # holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= holdout_start_date) & (df_5yr_join_cv.DATE <= holdout_end_date))
  train = df.filter((df.DATE >= train_start_date) & (df.DATE <= train_end_date))
  holdout = df.filter((df.DATE >= holdout_start_date) & (df.DATE <= holdout_end_date))
  
  train = train.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  holdout = holdout.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  
  # If we want to split to X and Y, use the code below
  #   train_X = train.select(feature_list)
  #   train_Y = train.select(['DEP_DEL15'])
  #   holdout_X = holdout.select(feature_list)
  #   holdout_Y = holdout.select(['DEP_DEL15'])
  
  print(f"flights in {cv_group[0]}: {train.count()}, flights in {cv_group[1]}: {holdout.count()}")
  
  return train, holdout

train0, holdout0 = CVSplit_full1(df_5yr_join_cv, cv_group_list[0], features_for_cv)
train1, holdout1 = CVSplit_full1(df_5yr_join_cv, cv_group_list[1], features_for_cv)
train2, holdout2 = CVSplit_full1(df_5yr_join_cv, cv_group_list[2], features_for_cv)
train3, holdout3 = CVSplit_full1(df_5yr_join_cv, cv_group_list[3], features_for_cv)
train4, holdout4 = CVSplit_full1(df_5yr_join_cv, cv_group_list[4], features_for_cv)
train5, holdout5 = CVSplit_full1(df_5yr_join_cv, cv_group_list[5], features_for_cv)
train6, holdout6 = CVSplit_full1(df_5yr_join_cv, cv_group_list[6], features_for_cv)
train7, holdout7 = CVSplit_full1(df_5yr_join_cv, cv_group_list[7], features_for_cv)
train8, holdout8 = CVSplit_full1(df_5yr_join_cv, cv_group_list[8], features_for_cv)

# have date column to check if the date is splitted correctly
test = df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])
trainAll = df_5yr_join_cv.filter(df_5yr_join_cv.DATE < df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])

print(f'test_start: ')
df_CV_date.collect()[0]['test_start']


latest_record test_start_ test_start train0_ train0 train1 train2 train3 train4 train5 train6 train7 train8 holdout0 holdout1 holdout2 holdout3 holdout4 holdout5 holdout6 holdout7 holdout8 2019-12-31T23:57:00.000+0000 2018-12-31 2019-01-01 2014-12-31 2015-01-01 2015-06-01 2015-11-01 2016-04-01 2016-09-01 2017-02-01 2017-07-01 2017-12-01 2018-05-01 2015-07-01 2015-12-01 2016-05-01 2016-10-01 2017-03-01 2017-08-01 2018-01-01 2018-06-01 2018-11-01

latest_record test_start_ ... holdout7 holdout8
0 2019-12-31 23:57:00 2018-12-31 ... 2018-06-01 2018-11-01

[1 rows x 22 columns]
train0_start: 2015-01-01, holdout0_start: 2015-07-01
train0_end: 2015-06-30, holdout0_end: 2015-08-31
flights in train0: 2791528, flights in holdout0: 998862
train1_start: 2015-06-01, holdout1_start: 2015-12-01
train1_end: 2015-11-30, holdout1_end: 2016-01-31
flights in train1: 2891951, flights in holdout1: 886528
train2_start: 2015-11-01, holdout2_start: 2016-05-01
train2_end: 2016-04-30, holdout2_end: 2016-06-30
flights in train2: 2686339, flights in holdout2: 936396
train3_start: 2016-04-01, holdout3_start: 2016-10-01
train3_end: 2016-09-30, holdout3_end: 2016-11-30
flights in train3: 2821407, flights in holdout3: 897367
train4_start: 2016-09-01, holdout4_start: 2017-03-01
train4_end: 2017-02-28, holdout4_end: 2017-04-30
flights in train4: 2638228, flights in holdout4: 920597
train5_start: 2017-02-01, holdout5_start: 2017-08-01
train5_end: 2017-07-31, holdout5_end: 2017-09-30
flights in train5: 2784433, flights in holdout5: 926848
train6_start: 2017-07-01, holdout6_start: 2018-01-01
train6_end: 2017-12-31, holdout6_end: 2018-02-28
flights in train6: 2808214, flights in holdout6: 1039475
train7_start: 2017-12-01, holdout7_start: 2018-06-01
train7_end: 2018-05-31, holdout7_end: 2018-07-31
flights in train7: 3280374, flights in holdout7: 1221159
train8_start: 2018-05-01, holdout8_start: 2018-11-01
train8_end: 2018-10-31, holdout8_end: 2018-12-31
flights in train8: 3645721, flights in holdout8: 1143588
test_start: 
Out[53]: datetime.date(2019, 1, 1)

In [0]:
# # Assuming to use df_5yr_join_cv as a clean dataset

# Features_for_cv = ['CRS_DEP_DATETIME_UTC_END'] + ['ORI_station_id'] + Outcomes_for_flights + Features_for_flights + Features_for_weathers
# print(Features_for_cv)

# # [[train_start, train_end],[holdout_start, holdout_end]]
# cv_date_list=[[['2015-01-01', '2015-06-30'],['2015-07-01','2015-08-31']],
#              [['2015-06-01', '2015-11-30'],['2015-12-01', '2016-01-31']],
#              [['2015-11-01', '2016-04-30'],['2016-05-01', '2016-06-30']],
#              [['2016-04-01', '2016-09-30'],['2016-10-01', '2016-11-30']],
#              [['2016-09-01', '2017-02-28'],['2017-03-01', '2017-04-30']],
#              [['2017-02-01', '2017-07-31'],['2017-08-01', '2017-09-30']],
#              [['2017-07-01', '2017-12-31'],['2018-01-01', '2018-02-28']],
#              [['2017-12-01', '2018-05-31'],['2018-06-01', '2018-07-31']],
#              [['2018-05-01', '2018-10-31'],['2018-11-01', '2018-12-31']]]
# test_start_date = '2019-01-01'


# def CVSplit_full2(date_list,feature_list):
#   train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= date_list[0][0]) & (df_5yr_join_cv.DATE <= date_list[0][1]))
#   holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= date_list[1][0]) & (df_5yr_join_cv.DATE <= date_list[1][1]))
  
#   if 'DEP_DEL15' in feature_list:
#     train = train.select(feature_list)
#     holdout = holdout.select(feature_list)
#   else:
#     train = train.select(feature_list + ['DEP_DEL15'])
#     holdout = holdout.select(feature_list + ['DEP_DEL15'])
  
#   train_X = train.select(feature_list)
#   train_Y = train.select(['DEP_DEL15'])
#   holdout_X = holdout.select(feature_list)
#   holdout_Y = holdout.select(['DEP_DEL15'])
  
#   return train.cache(), holdout.cache()

# train0, holdout0 = CVSplit_full2(cv_date_list[0], Features_for_cv)
# train1, holdout1 = CVSplit_full2(cv_date_list[1], Features_for_cv)
# train2, holdout2 = CVSplit_full2(cv_date_list[2], Features_for_cv)
# train3, holdout3 = CVSplit_full2(cv_date_list[3], Features_for_cv)
# train4, holdout4 = CVSplit_full2(cv_date_list[4], Features_for_cv)
# train5, holdout5 = CVSplit_full2(cv_date_list[5], Features_for_cv)
# train6, holdout6 = CVSplit_full2(cv_date_list[6], Features_for_cv)
# train7, holdout7 = CVSplit_full2(cv_date_list[7], Features_for_cv)
# train8, holdout8 = CVSplit_full2(cv_date_list[8], Features_for_cv)

# trainAll = df_5yr_join_cv.filter(df_5yr_join_cv.DATE < test_start_date).select(Features_for_cv).cache()
# test = df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= test_start_date).select(Features_for_cv).cache()

In [0]:
print(type(train0))

<class 'pyspark.sql.dataframe.DataFrame'>

In [0]:
trainAll.columns

Out[54]: ['DATE',
 'DEP_DEL15',
 'DISTANCE',
 'ORI_elevation',
 'DEST_elevation',
 'prior_dep_delayed',
 'previous_DEP_DELAY_NEW',
 'prior_arr_delayed',
 'previous_ARR_DELAY_NEW',
 'plane_is_here',
 'avg_carrier_delay_24hrs',
 'flights_sch_Today_ORIGIN',
 'flights_sch_Today_DEST',
 'avg_ori_airport_delay_24hrs',
 'daytime',
 'evening',
 'mid_atlantic',
 'south',
 'midwest',
 'southwest',
 'west',
 'pacific_islands',
 'atlantic_islands',
 'summer',
 'winter',
 'autumn',
 'weekend_or_holiday',
 'OC1_0_wind_gust_spd_rate_imp',
 'AA1_1_liquid_precip',
 'AA3_1_liquid_precip',
 'gd1_0_sky_coverage',
 'au2_4_extreme_wind_weather',
 'mv1_0_sand_dust_near',
 'mv1_0_thunder_rain_near',
 'aw1_mw1_0_smoke_haze_dust',
 'aw1_mw1_0_fog',
 'aw1_mw1_0_rain_drizzle',
 'aw1_mw1_0_freezing_rain_drizzle',
 'aw1_mw1_0_snow',
 'aw1_mw1_0_hail_or_ice',
 'aw1_mw1_0_thunderstorm',
 'aw1_mw1_0_tornado',
 'SLP_0_avg_station_press_imp',
 'WND_3_wind_speed_imp',
 'CIG_0_sky_ceiling_height_imp',
 'VIS_0_visibility_dist_imp',
 'TMP_0_air_temperature_imp',
 'DEW_0_dew_pt_temp_imp',
 'MA1_0_altimeter_set_rate_imp',
 'MA1_2_station_pres_rate_imp',
 'GD1_3_cloud_height_imp',
 'depDelayPageRank',
 'arrDelayPageRank']

In [0]:
trainAll.count()

Out[56]: 23829122

In [0]:
# bundle CV sets into lists and loop over zip of train, test. Keep running tracking array of recall, precision, f1 score. 
# if it works make it a wrapper function

# list of features(this list is updated everytime we change the features)
print(feature_list)
print(f"\nNumber of Features (Selected) in feature_list: {len(feature_list)}")

print(feature_list_full_0)
print(f"\nNumber of Features (Full) in feature_list_full_0: {len(feature_list_full_0)}")

# list of name of the dataset
cv_group_list = [[train0, holdout0],[train1, holdout1],[train2,holdout2],
                 [train3, holdout3],[train4, holdout4],[train5,holdout5],
                 [train6, holdout6],[train7, holdout7],[train8,holdout8]]

cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

['prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'evening', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank']

Number of Features (Selected) in feature_list: 10
['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

Number of Features (Full) in feature_list_full_0: 51

In [0]:
cv_result

Out[20]: [['CV_group', 'Accuracy', 'Recall', 'Precision', 'f1_score']]

## Define function that execute Random Forest from assembling to modeling

In [0]:
#RandomForestClassifier(*, featuresCol='features', labelCol='label', predictionCol='prediction', probabilityCol='probability', rawPredictionCol='rawPrediction', 
                        #maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                        #impurity='gini', numTrees=20, featureSubsetStrategy='auto', seed=None, subsamplingRate=1.0, leafCol='', minWeightFractionPerNode=0.0, 
                        #weightCol=None, bootstrap=True)

In [0]:
def RandomForestCV(train, holdout, feature_list, 
                   maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                   impurity='gini', numTrees=20, featureSubsetStrategy='auto', seed=12345, subsamplingRate=1.0, leafCol='', minWeightFractionPerNode=0.0, 
                   weightCol=None, bootstrap=True, 
                  CV_group=1, verbose=0): #all parameters are default
  
  # Assemble features
  assembler = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train = assembler.transform(train)
  assmb_holdout = assembler.transform(holdout)

  # modeling
  rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                              maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,
                              cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, featureSubsetStrategy=featureSubsetStrategy,
                              seed=seed, subsamplingRate=subsamplingRate, leafCol=leafCol, minWeightFractionPerNode=minWeightFractionPerNode, 
                              weightCol=weightCol, bootstrap=bootstrap)
  rfModel = rf.fit(assmb_train)
  predictions = rfModel.transform(assmb_holdout)
  
#   predictions.select('DEP_DEL15','normalized_features')

  results = predictions.select(['prediction', 'DEP_DEL15'])
  results = results.withColumnRenamed('DEP_DEL15', 'label')
  # display(results.head(5))
  metrics = MulticlassMetrics(results.rdd)

  # ['CV_group','Accuracy','Recall','Precision','f1_score']
  cv_result_run = [[CV_group, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]

  if verbose > 1:
    # Summary stats
    print(f'CV_group: {CV_group}, Accuracy: {metrics.accuracy}, Recall: {metrics.recall(label=1)},\
    Precision: {metrics.precision(1)}, F1_score: {metrics.fMeasure(1.0,1.0)}')
  
  return cv_result_run

#print(metrics.confusionMatrix().toArray())


In [0]:
def RandomForestCV_simple(train, holdout, feature_list, 
                   maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                   impurity='gini', numTrees=20, seed=12345, 
                  CV_group=1, verbose=0): #all parameters are default
  
  # Assemble features
  assembler = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train = assembler.transform(train)
  assmb_holdout = assembler.transform(holdout)

  # modeling
  rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                              maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,
                              cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, seed=seed)
  rfModel = rf.fit(assmb_train)
  predictions = rfModel.transform(assmb_holdout)
  
#   predictions.select('DEP_DEL15','normalized_features')

  results = predictions.select(['prediction', 'DEP_DEL15'])
  results = results.withColumnRenamed('DEP_DEL15', 'label')
  # display(results.head(5))
  metrics = MulticlassMetrics(results.rdd)

  # ['CV_group','Accuracy','Recall','Precision','f1_score']
  cv_result_run = [[CV_group, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]

  if verbose > 1:
    # Summary stats
    print(f'CV_group: {CV_group}, Accuracy: {metrics.accuracy}, Recall: {metrics.recall(label=1)},\
    Precision: {metrics.precision(1)}, F1_score: {metrics.fMeasure(1.0,1.0)}')
  
  return cv_result_run

#print(metrics.confusionMatrix().toArray())


In [0]:
display(train0)
display(holdout0)

DATE DEP_DEL15 DISTANCE ORI_elevation DEST_elevation prior_dep_delayed previous_DEP_DELAY_NEW prior_arr_delayed previous_ARR_DELAY_NEW plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs daytime evening mid_atlantic south midwest southwest west pacific_islands atlantic_islands summer winter autumn weekend_or_holiday OC1_0_wind_gust_spd_rate_imp AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank 2015-01-01T07:51:00.000+0000 1.0 1598.0 13.0 841.0 0 0.0 0 0.0 0 0.12 274 83 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 759.0 15.0 96.0 0 0.0 0 0.0 0 0.27 178 391 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 1547.0 1026.0 841.0 0 0.0 0 0.0 1 0.17 997 63 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 842.0 26.0 146.0 0 6.0 0 0.0 0 0.25 173 187 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T07:51:00.000+0000 1.0 1089.0 13.0 8.0 0 0.0 0 0.0 0 0.17 274 208 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 547.0 15.0 1026.0 0 0.0 0 0.0 0 0.26 178 912 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 1747.0 1026.0 2181.0 1 24.0 1 16.0 1 0.17 997 373 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 507.0 26.0 748.0 0 0.0 0 0.0 0 0.23 173 243 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T07:51:00.000+0000 0.0 1576.0 13.0 841.0 0 0.0 0 0.0 0 0.12 274 6 0.13 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10212.0 62.0 22000.0 16093.0 -17.0 -117.0 10213.0 10205.0 4267.0 0.011232755660359141 0.01124578131448836 2015-03-28T21:52:00.000+0000 0.0 1184.0 15.0 487.0 0 5.0 0 0.0 0 0.26 178 116 0.13 0 1 0 1 0 0 0 0 0 0 0 0 1 103 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10190.0 62.0 1829.0 16093.0 22.0 -122.0 10193.0 10169.0 1829.0 0.00522208583229352 0.0054210976594481165 2015-02-04T10:52:00.000+0000 0.0 332.0 1026.0 341.0 0 0.0 0 0.0 0 0.17 997 43 0.13 1 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10250.0 0.0 7620.0 16093.0 22.0 -39.0 10244.0 9870.0 6096.0 0.033239075606230094 0.030960773935925966 2015-01-31T13:53:00.000+0000 0.0 406.0 26.0 1026.0 0 0.0 0 0.0 0 0.14 173 678 0.14 1 0 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 10255.0 36.0 8230.0 16093.0 111.0 28.0 10254.0 10250.0 8230.0 0.008705084476392696 0.009964207517866688 2015-01-01T09:00:00.000+0000 0.0 944.0 13.0 96.0 0 0.0 0 0.0 0 0.12 274 303 0.13 1 0 1 0 0 0 0 0 0 

DATE DEP_DEL15 DISTANCE ORI_elevation DEST_elevation prior_dep_delayed previous_DEP_DELAY_NEW prior_arr_delayed previous_ARR_DELAY_NEW plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs daytime evening mid_atlantic south midwest southwest west pacific_islands atlantic_islands summer winter autumn weekend_or_holiday OC1_0_wind_gust_spd_rate_imp AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank 2015-07-05T21:53:00.000+0000 1.0 1046.0 9.0 841.0 0 2.0 0 0.0 0 0.1 208 82 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 177.0 9.0 96.0 0 11.0 0 3.0 1 0.19 208 320 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 1127.0 9.0 645.0 0 0.0 0 0.0 0 0.19 208 330 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 1119.0 9.0 607.0 0 0.0 0 0.0 1 0.19 208 705 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 925.0 9.0 146.0 0 0.0 0 0.0 1 0.19 208 276 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 1.0 899.0 9.0 15.0 0 0.0 0 0.0 1 0.06 208 215 0.07 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 977.0 9.0 75.0 0 0.0 0 0.0 0 0.19 208 11 0.07 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 2173.0 9.0 2181.0 0 1.0 0 4.0 1 0.19 208 409 0.07 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 1.0 899.0 9.0 15.0 1 66.0 0 0.0 0 0.12 208 215 0.07 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T21:53:00.000+0000 0.0 1173.0 9.0 173.0 0 0.0 0 3.0 1 0.07 208 57 0.07 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10192.0 67.0 22000.0 14484.0 311.0 239.0 10193.0 10189.0 914.0 0.010437066772075025 0.010258001983731417 2015-07-05T22:53:00.000+0000 1.0 1092.0 9.0 99.0 0 0.0 0 0.0 0 0.11 208 13 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10190.0 67.0 22000.0 14484.0 306.0 244.0 10190.0 10186.0 884.0 0.010437066772075025 0.010258001983731417 2015-07-05T22:53:00.000+0000 0.0 1065.0 9.0 18.0 0 11.0 0 0.0 0 0.12 208 296 0.08 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10190.0 67.0 22000.0 14484.0 306.0 244.0 10190.0 10186.0 884.0 0.010437066772075025 0.010258001983731417 2015-07-05T22:53:00.000+0000 0.0 1703.0 9.0 5431.0 0 5.0 0 0.0 0 0.11 208 616 0.09 0 1 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 

## Run cross validation

In [0]:
def runCV_RandomForest(cv_dataset, feature_list, verbose=0, rebalance_input_tup=(False, 4.545),
                      maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                      impurity='gini', numTrees=20, featureSubsetStrategy='auto', seed=12345, subsamplingRate=1.0, leafCol='', minWeightFractionPerNode=0.0, 
                      weightCol=None, bootstrap=True):
  """
  Wrapper function to run Random Forest cross validation.
  Inputs:
  - cv_dataset: list of lists of test & holdout.
  - feature_list: list of str names of features
  - verbose: [0, 1, 2] as verbosity level. 0 means nothing printed. 1 means summary stats printed. 2 means everything printed.
  - rebalance_input_tup: To be updated
  - rest of the parameters: hyperparameters for RF
  Outputs:
  - df_cv_result_0: pandas dataframe of each CV result
  - mean_pd_df: pandas dataframe of the mean of the CV results. This is what we look at to assess performance of CV.
  """
  if rebalance_input_tup[0]:
    rebalancing, desired_neg_to_pos_ratio = rebalance_input_tup
    rebalancing = True
  else:
    rebalancing = False
  
  def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
    original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
    positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
    negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

    # undersampling the negative cases
    negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
    positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
    new_trainDF = positiveDF.union(negativeDF).cache()
    return new_trainDF
  
  print(f"Random Forest, maxDepth={maxDepth}, maxBins={maxBins},minInstancesPerNode={minInstancesPerNode}, minInfoGain={minInfoGain}, maxMemoryInMB={maxMemoryInMB},\
                              cacheNodeIds={cacheNodeIds}, checkpointInterval={checkpointInterval}, impurity={impurity}, numTrees={numTrees},\
                              featureSubsetStrategy={featureSubsetStrategy}, seed={seed}, subsamplingRate={subsamplingRate}, leafCol={leafCol},\
                              minWeightFractionPerNode={minWeightFractionPerNode}, weightCol={weightCol}, bootstrap={bootstrap}")
  
  # instantiate pandas bookkeeping of metrics
  cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]
  
  num_cv = len(cv_dataset)
  maxDepth_lst = [maxDepth]*num_cv
  maxBins_lst = [maxBins]*num_cv
  minInstancesPerNode_lst = [minInstancesPerNode]*num_cv
#   minInfoGain_lst = [minInfoGain]*num_cv
#   maxMemoryInMB_lst = [maxMemoryInMB]*num_cv
#   cacheNodeIds_lst = [cacheNodeIds]*num_cv
#   checkpointInterval_lst = [checkpointInterval]*num_cv
#   impurity_lst = [impurity]*num_cv
  numTrees_lst = [numTrees]*num_cv
#   featureSubsetStrategy_lst = [featureSubsetStrategy]*num_cv
#   seed_lst = [seed]*num_cv
#   subsamplingRate_lst = [subsamplingRate]*num_cv
#   leafCol_lst = [leafCol]*num_cv
#   minWeightFractionPerNode_lst = [minWeightFractionPerNode]*num_cv
#   weightCol_lst = [weightCol]*num_cv
#   bootstrap_lst = [bootstrap]*num_cv
  times = []
  
  for i in range(len(cv_dataset)):
    if verbose > 1:
      print(f"Training CV {i}...")
    if not rebalancing:
      start = time.time()
      cv_result += RandomForestCV(train=cv_dataset[i][0], holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, featureSubsetStrategy=featureSubsetStrategy, seed=seed, subsamplingRate=subsamplingRate, leafCol=leafCol, minWeightFractionPerNode=minWeightFractionPerNode, weightCol=weightCol, bootstrap=bootstrap,
                                 CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
    else:
      start = time.time()
      # rebalance cv_dataset[i][0]
      new_trainDF = rebalanceDF(cv_dataset[i][0], desired_neg_to_pos_ratio)
      
      cv_result += RandomForestCV(train=new_trainDF, holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, featureSubsetStrategy=featureSubsetStrategy, seed=seed, subsamplingRate=subsamplingRate, leafCol=leafCol, minWeightFractionPerNode=minWeightFractionPerNode, weightCol=weightCol, bootstrap=bootstrap, 
                                  CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
  
  # append columns for tuned hyperparameters
  df_cv_result_0 = pd.DataFrame(cv_result[1:],columns=cv_result[0])
  df_cv_result_0["maxDepth"] = maxDepth_lst
  df_cv_result_0["maxBins"] = maxBins_lst
  df_cv_result_0["minInstancesPerNode"] = minInstancesPerNode_lst
  df_cv_result_0["numTrees"] = numTrees_lst
  df_cv_result_0["time"] = times
  
  if verbose > 1:
    display(df_cv_result_0)
  
  # make the means_df
  mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  
  if verbose > 0:
    display(mean_pd_df)
  return df_cv_result_0, mean_pd_df

In [0]:
def runCV_RandomForest_simple(cv_dataset, feature_list, verbose=0, rebalance_input_tup=(False, 4.545),
                      maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                       impurity='gini', numTrees=20, seed=12345):
  """
  Wrapper function to run Random Forest cross validation.
  Inputs:
  - cv_dataset: list of lists of test & holdout.
  - feature_list: list of str names of features
  - verbose: [0, 1, 2] as verbosity level. 0 means nothing printed. 1 means summary stats printed. 2 means everything printed.
  - rebalance_input_tup: To be updated
  - rest of the parameters: hyperparameters for RF
  Outputs:
  - df_cv_result_0: pandas dataframe of each CV result
  - mean_pd_df: pandas dataframe of the mean of the CV results. This is what we look at to assess performance of CV.
  """
  if rebalance_input_tup[0]:
    rebalancing, desired_neg_to_pos_ratio = rebalance_input_tup
    rebalancing = True
    rebalancing_ratio_lst = [desired_neg_to_pos_ratio]*len(cv_dataset)
  else:
    rebalancing = False
  
  def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
    original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
    positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
    negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

    # undersampling the negative cases
    negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
    positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
    new_trainDF = positiveDF.union(negativeDF).cache()
    return new_trainDF
  
  print(f"Random Forest, maxDepth={maxDepth}, maxBins={maxBins}, minInstancesPerNode={minInstancesPerNode}, minInfoGain={minInfoGain}, maxMemoryInMB={maxMemoryInMB}, cacheNodeIds={cacheNodeIds}, checkpointInterval={checkpointInterval}, impurity={impurity}, numTrees={numTrees}, seed={seed}")
  
  # instantiate pandas bookkeeping of metrics
  cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]
  
  num_cv = len(cv_dataset)
  maxDepth_lst = [maxDepth]*num_cv
  maxBins_lst = [maxBins]*num_cv
  minInstancesPerNode_lst = [minInstancesPerNode]*num_cv
#   minInfoGain_lst = [minInfoGain]*num_cv
#   maxMemoryInMB_lst = [maxMemoryInMB]*num_cv
#   cacheNodeIds_lst = [cacheNodeIds]*num_cv
#   checkpointInterval_lst = [checkpointInterval]*num_cv
#   impurity_lst = [impurity]*num_cv
  numTrees_lst = [numTrees]*num_cv
#   seed_lst = [seed]*num_cv
  times = []
  
  for i in range(len(cv_dataset)):
    if verbose > 1:
      print(f"Training CV {i}...")
    if not rebalancing:
      start = time.time()
      cv_result += RandomForestCV_simple(train=cv_dataset[i][0], holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, seed=seed,
                                 CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
    else:
      start = time.time()
      # rebalance cv_dataset[i][0]
      new_trainDF = rebalanceDF(cv_dataset[i][0], desired_neg_to_pos_ratio)
      
      cv_result += RandomForestCV_simple(train=new_trainDF, holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, minInfoGain=minInfoGain, maxMemoryInMB=maxMemoryInMB,cacheNodeIds=cacheNodeIds, checkpointInterval=checkpointInterval, impurity=impurity, numTrees=numTrees, seed=seed,
                                 CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
  
  # append columns for tuned hyperparameters
  df_cv_result_0 = pd.DataFrame(cv_result[1:],columns=cv_result[0])
  df_cv_result_0["maxDepth"] = maxDepth_lst
  df_cv_result_0["maxBins"] = maxBins_lst
  df_cv_result_0["minInstancesPerNode"] = minInstancesPerNode_lst
  df_cv_result_0["numTrees"] = numTrees_lst
  df_cv_result_0["time"] = times
  
  if rebalancing:
    df_cv_result_0["desired_neg_to_pos_ratio"] = rebalancing_ratio_lst
  
  if verbose > 1:
    display(df_cv_result_0)
  
  # make the means_df
  if rebalancing:
    mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'desired_neg_to_pos_ratio'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'desired_neg_to_pos_ratio', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  else:
    mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  
  if verbose > 0:
    display(mean_pd_df)
  return df_cv_result_0, mean_pd_df

In [0]:
print(feature_list)

['prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'evening', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
print(feature_list_full_0)

['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
print(cv_group_list)

[[DataFrame[DATE: timestamp, DEP_DEL15: double, DISTANCE: double, ORI_elevation: double, DEST_elevation: double, prior_dep_delayed: int, previous_DEP_DELAY_NEW: double, prior_arr_delayed: int, previous_ARR_DELAY_NEW: double, plane_is_here: int, avg_carrier_delay_24hrs: double, flights_sch_Today_ORIGIN: bigint, flights_sch_Today_DEST: bigint, avg_ori_airport_delay_24hrs: double, daytime: int, evening: int, mid_atlantic: int, south: int, midwest: int, southwest: int, west: int, pacific_islands: int, atlantic_islands: int, summer: int, winter: int, autumn: int, weekend_or_holiday: int, OC1_0_wind_gust_spd_rate_imp: int, AA1_1_liquid_precip: int, AA3_1_liquid_precip: int, gd1_0_sky_coverage: int, au2_4_extreme_wind_weather: int, mv1_0_sand_dust_near: int, mv1_0_thunder_rain_near: int, aw1_mw1_0_smoke_haze_dust: int, aw1_mw1_0_fog: int, aw1_mw1_0_rain_drizzle: int, aw1_mw1_0_freezing_rain_drizzle: int, aw1_mw1_0_snow: int, aw1_mw1_0_hail_or_ice: int, aw1_mw1_0_thunderstorm: int, aw1_mw1_0_tornado: int, SLP_0_avg_station_press_imp: double, WND_3_wind_speed_imp: double, CIG_0_sky_ceiling_height_imp: double, VIS_0_visibility_dist_imp: double, TMP_0_air_temperature_imp: double, DEW_0_dew_pt_temp_imp: double, MA1_0_altimeter_set_rate_imp: double, MA1_2_station_pres_rate_imp: double, GD1_3_cloud_height_imp: double, depDelayPageRank: double, arrDelayPageRank: double], DataFrame[DATE: timestamp, DEP_DEL15: double, DISTANCE: double, ORI_elevation: double, DEST_elevation: double, prior_dep_delayed: int, previous_DEP_DELAY_NEW: double, prior_arr_delayed: int, previous_ARR_DELAY_NEW: double, plane_is_here: int, avg_carrier_delay_24hrs: double, flights_sch_Today_ORIGIN: bigint, flights_sch_Today_DEST: bigint, avg_ori_airport_delay_24hrs: double, daytime: int, evening: int, mid_atlantic: int, south: int, midwest: int, southwest: int, west: int, pacific_islands: int, atlantic_islands: int, summer: int, winter: int, autumn: int, weekend_or_holiday: int, OC1_0_wind_gust_spd_rate_imp: int, AA1_1_liquid_precip: int, AA3_1_liquid_precip: int, gd1_0_sky_coverage: int, au2_4_extreme_wind_weather: int, mv1_0_sand_dust_near: int, mv1_0_thunder_rain_near: int, aw1_mw1_0_smoke_haze_dust: int, aw1_mw1_0_fog: int, aw1_mw1_0_rain_drizzle: int, aw1_mw1_0_freezing_rain_drizzle: int, aw1_mw1_0_snow: int, aw1_mw1_0_hail_or_ice: int, aw1_mw1_0_thunderstorm: int, aw1_mw1_0_tornado: int, SLP_0_avg_station_press_imp: double, WND_3_wind_speed_imp: double, CIG_0_sky_ceiling_height_imp: double, VIS_0_visibility_dist_imp: double, TMP_0_air_temperature_imp: double, DEW_0_dew_pt_temp_imp: double, MA1_0_altimeter_set_rate_imp: double, MA1_2_station_pres_rate_imp: double, GD1_3_cloud_height_imp: double, depDelayPageRank: double, arrDelayPageRank: double]], [DataFrame[DATE: timestamp, DEP_DEL15: double, DISTANCE: double, ORI_elevation: double, DEST_elevation: double, prior_dep_delayed: int, previous_DEP_DELAY_NEW: double, prior_arr_delayed: int, previous_ARR_DELAY_NEW: double, plane_is_here: int, avg_carrier_delay_24hrs: double, flights_sch_Today_ORIGIN: bigint, flights_sch_Today_DEST: bigint, avg_ori_airport_delay_24hrs: double, daytime: int, evening: int, mid_atlantic: int, south: int, midwest: int, southwest: int, west: int, pacific_islands: int, atlantic_islands: int, summer: int, winter: int, autumn: int, weekend_or_holiday: int, OC1_0_wind_gust_spd_rate_imp: int, AA1_1_liquid_precip: int, AA3_1_liquid_precip: int, gd1_0_sky_coverage: int, au2_4_extreme_wind_weather: int, mv1_0_sand_dust_near: int, mv1_0_thunder_rain_near: int, aw1_mw1_0_smoke_haze_dust: int, aw1_mw1_0_fog: int, aw1_mw1_0_rain_drizzle: int, aw1_mw1_0_freezing_rain_drizzle: int, aw1_mw1_0_snow: int, aw1_mw1_0_hail_or_ice: int, aw1_mw1_0_thunderstorm: int, aw1_mw1_0_tornado: int, SLP_0_avg_station_press_imp: double, WND_3_wind_speed_imp: double, CIG_0_sky_ceiling_height_imp: double, VIS_0_visibility_dist_imp: double, TMP_0_air_temperature_imp: double, DEW_0_dew_pt_temp_imp: double, MA1_0_altimeter_set_rate_

In [0]:
CV_group = 1
verbose = 2

# Assemble features
assembler_tmp = VectorAssembler().setInputCols(feature_list)\
                          .setOutputCol('features')

assmb_train_tmp = assembler_tmp.transform(train0)
assmb_holdout_tmp = assembler_tmp.transform(holdout0)

# modeling
rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=6, maxBins=64, minInstancesPerNode=100, numTrees=20, seed=12345)

rfModel = rf.fit(assmb_train_tmp)
predictions = rfModel.transform(assmb_holdout_tmp)

results = predictions.select(['prediction', 'DEP_DEL15'])
results = results.withColumnRenamed('DEP_DEL15', 'label')
# display(results.head(5))
metrics = MulticlassMetrics(results.rdd)

# ['CV_group','Accuracy','Recall','Precision','f1_score']
cv_result_run = [[CV_group, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]

if verbose > 1:
  # Summary stats
  print(f'CV_group: {CV_group}, Accuracy: {metrics.accuracy}, Recall: {metrics.recall(label=1)},\
  Precision: {metrics.precision(1)}, F1_score: {metrics.fMeasure(1.0,1.0)}')

CV_group: 1, Accuracy: 0.8377914066207344, Recall: 0.29258436047686404, Precision: 0.7625849378941825, F1_score: 0.4229092463313862

In [0]:
# test the function to run RF once
temp = RandomForestCV_simple(train=train0, holdout=holdout0, feature_list=feature_list, maxDepth=6, maxBins=64, minInstancesPerNode=100, numTrees=20, CV_group=1, verbose=2) #all parameters are default
  
print(temp)


CV_group: 1, Accuracy: 0.8377914066207344, Recall: 0.29258436047686404, Precision: 0.7625849378941825, F1_score: 0.4229092463313862
[[1, 0.8377914066207344, 0.29258436047686404, 0.7625849378941825, 0.4229092463313862]]

In [0]:
# test the function to run RF once
temp = RandomForestCV_simple(train=train0, holdout=holdout0, feature_list=feature_list, maxDepth=6, maxBins=64, minInstancesPerNode=100, numTrees=20, CV_group=1, verbose=2, cacheNodeIds=True) 
  
print(temp)


CV_group: 1, Accuracy: 0.8377914066207344, Recall: 0.29258436047686404, Precision: 0.7625849378941825, F1_score: 0.4229092463313862
[[1, 0.8377914066207344, 0.29258436047686404, 0.7625849378941825, 0.4229092463313862]]

In [0]:
# runCV_LogReg(cv_dataset=cv_group_list, feature_list=feature_list, maxIter_input=15, regParam_input=0, elasticNetParam_input=0, verbose=2, rebalance_input_tup=(True, 1.6))

df_cv_result_0, mean_pd_df = runCV_RandomForest_simple(cv_dataset=cv_group_list, feature_list=feature_list, verbose=0, rebalance_input_tup=(True, 1.6),
                                                maxDepth=6, maxBins=64, minInstancesPerNode=100, numTrees=20)

print(df_cv_result_0)
print(mean_pd_df)

Random Forest, maxDepth=6, maxBins=64, minInstancesPerNode=100, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10, impurity=gini, numTrees=20, seed=12345
 CV_group Accuracy Recall ... numTrees time desired_neg_to_pos_ratio
0 0 0.816066 0.422342 ... 20 465.295880 1.6
1 1 0.821628 0.447294 ... 20 291.998706 1.6
2 2 0.823381 0.426308 ... 20 323.973187 1.6
3 3 0.873218 0.328493 ... 20 47.230498 1.6
4 4 0.830023 0.429802 ... 20 44.927446 1.6
5 5 0.845792 0.401383 ... 20 42.969869 1.6
6 6 0.823173 0.438026 ... 20 37.803277 1.6
7 7 0.804994 0.470388 ... 20 30.745605 1.6
8 8 0.836344 0.421837 ... 20 252.518269 1.6

[9 rows x 11 columns]
 maxDepth ... time
maxDepth maxBins minInstancesPerNode numTrees desired_neg_to_pos_ratio ... 
6 64 100 20 1.6 6 ... 170.829193

[1 rows x 10 columns]

In [0]:
display(df_cv_result_0)

CV_group Accuracy Recall Precision f1_score maxDepth maxBins minInstancesPerNode numTrees time desired_neg_to_pos_ratio 0 0.816065682746966 0.4223420350994781 0.5630181985414887 0.4826382142324122 6 64 100 20 465.29587984085083 1.6 1 0.821627743286168 0.44729387656702024 0.5276873195773667 0.4841761209804216 6 64 100 20 291.9987063407898 1.6 2 0.8233813472078052 0.4263076169165097 0.5142000541225734 0.4661469681563614 6 64 100 20 323.9731867313385 1.6 3 0.8732179810490023 0.32849262541834146 0.5352983090794486 0.4071391349661282 6 64 100 20 47.23049831390381 1.6 4 0.8300233435477196 0.42980216410649524 0.5493890903060955 0.48229315547085916 6 64 100 20 44.927446126937866 1.6 5 0.845792406090319 0.4013833026350412 0.5748844721611557 0.47271667472137474 6 64 100 20 42.96986937522888 1.6 6 0.8231732364895741 0.4380259690581435 0.5137620967490668 0.47288077751426005 6 64 100 20 37.80327653884888 1.6 7 0.8049942718351992 0.47038849835901747 0.5585155154435295 0.5106779079396456 6 64 100 20 30.745604991912842 1.6 8 0.8363440329909023 0.42183683799283506 0.5525800803378309 0.47843716471358705 6 64 100 20 252.51826906204224 1.6

In [0]:
display(mean_pd_df)

maxDepth maxBins minInstancesPerNode numTrees desired_neg_to_pos_ratio Accuracy Recall Precision f1_score time 6 64 100 20 1.5999999999999999 0.8305133383604062 0.4206525473503202 0.5432594595909508 0.47301179096611673 170.8291930357615

In [0]:
CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, 5, 0, 0)

## 4.0. Tuning the Rebalancing Ratio

In [0]:
maxIter_options = [15]
regParam_options = [0]
elasticNetParam_options = [0]
desired_neg_to_pos_ratio_options = [0.7, 1, 1.3, 1.6, 1.9, 2.1, 2.4, 2.7, 3.0]

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []
desired_neg_to_pos_ratio_values = []

for desired_neg_to_pos_ratio in desired_neg_to_pos_ratio_options:
  for maxIter_val in maxIter_options:
    for regParam_val in regParam_options:
      for elasticNetParam_val in elasticNetParam_options:
        # run the CV
        CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, 
                                                   verbose=0, rebalance_input_tup=(True, desired_neg_to_pos_ratio))
        # save results to lists of pandas DFs
        total_cv_dfs_lst.append(CV_all_pd_df)
        mean_cv_dfs_lst.append(CV_mean_pd_df)
        desired_neg_to_pos_ratio_values.append(desired_neg_to_pos_ratio)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf['desired_neg_to_pos_ratio'] = desired_neg_to_pos_ratio_values
display(mean_cv_pddf)

In [0]:
desired_neg_to_pos_ratio_best = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['desired_neg_to_pos_ratio']
print(f"The best desired negative to positive ratio for rebalancing: {desired_neg_to_pos_ratio_best}")

## 4.1. Tuning the Max Number of Iterations

In [0]:
maxIter_options = [10, 15, 20, 25, 30, 35, 40, 45, 50]
regParam_options = [0]
elasticNetParam_options = [0]

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for maxIter_val in maxIter_options:
  for regParam_val in regParam_options:
    for elasticNetParam_val in elasticNetParam_options:
      # run the CV
      CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, 
                                                 verbose=0, rebalance_input_tup=(True, desired_neg_to_pos_ratio_best))
      # save results to lists of pandas DFs
      total_cv_dfs_lst.append(CV_all_pd_df)
      mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf['desired_neg_to_pos_ratio'] = [desired_neg_to_pos_ratio_best]*len(maxIter_options)
display(mean_cv_pddf)

In [0]:
maxIter_best = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['maxIter']
print(f"The best maxIter value: {maxIter_best}")

In [0]:
mean_cv_maxIter_sparkDF=spark.createDataFrame(mean_cv_pddf) 
mean_cv_maxIter_sparkDF.printSchema()
mean_cv_maxIter_sparkDF.show()

mean_cv_maxIter_sparkDF.write.parquet(f"{blob_url}/CV_results_maxIter_baseline_RFselection_3-30-22")

In [0]:
# Plot of MaxIter vs the metric F-1 score (Maybe Precision & Recall too?)
df_maxIter_CVresults = spark.read.parquet(f'{blob_url}/CV_results_maxIter_baseline_3-29-22')

## 4.2. Tuning the Regularization Parameter (L2)

In [0]:
maxIter_options = [maxIter_best]
regParam_options = [0, 0.001, 0.0025, 0.005, 0.01, 0.025, 0.05, 0.1, 0.5, 1, 5, 10]
elasticNetParam_options = [0] # L2

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for maxIter_val in maxIter_options:
  for regParam_val in regParam_options:
    for elasticNetParam_val in elasticNetParam_options:
      # run the CV
      CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, 
                                                 verbose=0, rebalance_input_tup=(True, desired_neg_to_pos_ratio_best))
      # save results to lists of pandas DFs
      total_cv_dfs_lst.append(CV_all_pd_df)
      mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf['desired_neg_to_pos_ratio'] = [desired_neg_to_pos_ratio_best]*len(regParam_options)
display(mean_cv_pddf)

In [0]:
regParam_best = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['regParam']
print(f"The best regParam value (L2): {regParam_best}")

In [0]:
mean_cv_regParam_sparkDF=spark.createDataFrame(mean_cv_pddf) 
mean_cv_regParam_sparkDF.printSchema()
mean_cv_regParam_sparkDF.show()

mean_cv_regParam_sparkDF.write.parquet(f"{blob_url}/CV_results_regParam_baseline_RFselection_3-30-22")

##### Tuning both Regularization Parameter & Elastic Tuning Together

In [0]:
# hard-coding best values
maxIter_best = 10
desired_neg_to_pos_ratio_best = 1.6

In [0]:
maxIter_options = [maxIter_best] # 10
regParam_options = [0.001, 0.005, 0.01, 0.05, 0.1]
elasticNetParam_options = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8] 

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for maxIter_val in maxIter_options:
  for regParam_val in regParam_options:
    for elasticNetParam_val in elasticNetParam_options:
      # run the CV
      CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, 
                                                 verbose=0, rebalance_input_tup=(True, desired_neg_to_pos_ratio_best))
      # save results to lists of pandas DFs
      total_cv_dfs_lst.append(CV_all_pd_df)
      mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf['desired_neg_to_pos_ratio'] = [desired_neg_to_pos_ratio_best]*(len(regParam_options)*len(elasticNetParam_options))
display(mean_cv_pddf)

In [0]:
# value to beat: 0.47306982860305297, 0 regParam, 0 elasticNetParam
regParam_best_2 = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['regParam']
print(f"The best regParam value: {regParam_best_2}")

elasticNetParam_best_2 = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['elasticNetParam']
print(f"The best elasticNetParam value: {elasticNetParam_best_2}")

In [0]:
mean_cv_regParam_sparkDF=spark.createDataFrame(mean_cv_pddf) 
mean_cv_regParam_sparkDF.printSchema()
mean_cv_regParam_sparkDF.show()

mean_cv_regParam_sparkDF.write.parquet(f"{blob_url}/CV_results_regParam&elasticNetParam_baseline_3-30-22")

## 4.3. Tuning the Elastic Net Parameter

In [0]:
maxIter_options = [maxIter_best]
regParam_options = [regParam_best]
elasticNetParam_options = [0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1]

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for maxIter_val in maxIter_options:
  for regParam_val in regParam_options:
    for elasticNetParam_val in elasticNetParam_options:
      # run the CV
      CV_all_pd_df, CV_mean_pd_df = runCV_LogReg(cv_group_list, feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, 
                                                 verbose=0, rebalance_input_tup=(True, desired_neg_to_pos_ratio_best))
      # save results to lists of pandas DFs
      total_cv_dfs_lst.append(CV_all_pd_df)
      mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf['desired_neg_to_pos_ratio'] = [desired_neg_to_pos_ratio_best]*len(elasticNetParam_options)
display(mean_cv_pddf)

In [0]:
elasticNetParam_best = mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['elasticNetParam']
print(f"The best elasticNetParam value: {elasticNetParam_best}")

In [0]:
mean_cv_elasticNetParam_sparkDF=spark.createDataFrame(mean_cv_pddf) 
mean_cv_elasticNetParam_sparkDF.printSchema()
mean_cv_elasticNetParam_sparkDF.show()

mean_cv_regParam_sparkDF.write.parquet(f"{blob_url}/CV_results_elasticNetParam_baseline_RFselection_3-30-22")

# 5. Result

#### Run on 2019 test set

In [0]:
feature_list

In [0]:
print(f"Number of Features: {len(feature_list)}")

In [0]:
display(df_5yr_join_cv)
print(test_start_date)
display(df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= test_start_date).select(Features_for_cv))

In [0]:
display(trainAll)
display(test)

In [0]:
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

cv_result += LogRegCV(train=trainAll, holdout=test, feature_list=feature_list, maxIter_input=15, regParam_input=0, elasticNetParam_input=0.0, CV_group=1, verbose=2)

df_cv_result_2019test = pd.DataFrame(cv_result[1:],columns=cv_result[0])

display(df_cv_result_2019test)

In [0]:
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

cv_result += LogRegCV(train=trainAll, holdout=test, feature_list=feature_list, maxIter_input=15, regParam_input=0.0025, elasticNetParam_input=0.1, CV_group=1, verbose=2)

df_cv_result_2019test = pd.DataFrame(cv_result[1:],columns=cv_result[0])

display(df_cv_result_2019test)

#### Rebalance the dataset
The training dataset contains many negatives (no delays) than positives (delays). The current ratio of counts in the training data are shown below. We should rebalance the training data, either through undersampling the negatives or oversampling the positives. The implementation below will undersample the negatives, or no delay, flights to a desired ratio of negatives to positives. This ratio is another tuning parameter, and we choose 1 for roughly equal number of positives and negatives in our training data.

In [0]:
display(trainAll.groupby('DEP_DEL15').count())
# positiveTrainCount = trainAll.groupby('DEP_DEL15').count()[].filter(WND_3_speed_rate_avg.ORI_station_id ==  '70026027502').select(['avg(WND_3)']).head()[0]

In [0]:
original_dep_del15_count_df = trainAll.groupby('DEP_DEL15').count()
positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
print(f"positive counts in training: {positiveTrainCount}")
negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]
print(f"negative counts in training: {negativeTrainCount}")

In [0]:
# desired_neg_to_pos_ratio = 1.6 # the desired ratio of negatives to positives
desired_neg_to_pos_ratio = desired_neg_to_pos_ratio_best

# undersampling the negative cases
negativeDF = trainAll.filter(trainAll['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
positiveDF = trainAll.filter(trainAll['DEP_DEL15']==1)
new_trainDF = positiveDF.union(negativeDF).cache()
display(new_trainDF.groupby('DEP_DEL15').count())

In [0]:
# Running with the best results from Tuning
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

cv_result += LogRegCV(train=new_trainDF, holdout=test, feature_list=feature_list, maxIter_input=maxIter_best, regParam_input=regParam_best, elasticNetParam_input=elasticNetParam_best, 
                      CV_group=1, verbose=2)

df_cv_result_2019_rebalanced_best = pd.DataFrame(cv_result[1:],columns=cv_result[0])

display(df_cv_result_2019_rebalanced_best)

In [0]:
## Where we run on 2019, with results from tuning both RegParam and elasticNetParam together.
maxIter_best = 10
regParam_best_2 = 0.001
elasticNetParam_best_2 = 0.5
desired_neg_to_pos_ratio_best = 1.6

cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

cv_result += LogRegCV(train=new_trainDF, holdout=test, feature_list=feature_list, maxIter_input=maxIter_best, regParam_input=regParam_best_2, elasticNetParam_input=elasticNetParam_best_2, 
                      CV_group=1, verbose=2)

df_cv_result_2019_rebalanced_best2 = pd.DataFrame(cv_result[1:],columns=cv_result[0])

display(df_cv_result_2019_rebalanced_best2)

In [0]:
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

cv_result += LogRegCV(train=new_trainDF, holdout=test, feature_list=feature_list, maxIter_input=10, regParam_input=0, elasticNetParam_input=0, CV_group=1, verbose=2)

df_cv_result_2019_rebalanced = pd.DataFrame(cv_result[1:],columns=cv_result[0])

display(df_cv_result_2019_rebalanced)

In [0]:
df_cv_result_2019_rebalanced.loc[df_cv_result_2019_rebalanced['f1_score'].idxmax()]['CV_group']

##### Testing Rebalancing

In [0]:
maxIter_options = [15]
regParam_options = [0]
elasticNetParam_options = [0]
ratio_params = [0.7, 0.8, 0.9, 1, 1.1, 1.2, 1.3]

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for desired_neg_to_pos_ratio in ratio_params:
  negativeDF = trainAll.filter(trainAll['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
  positiveDF = trainAll.filter(trainAll['DEP_DEL15']==1)
  new_trainDF = positiveDF.union(negativeDF).cache()
  for maxIter_val in maxIter_options:
    for regParam_val in regParam_options:
      for elasticNetParam_val in elasticNetParam_options:
        # run the CV
        CV_all_pd_df, CV_mean_pd_df = runCV_LogReg([[new_trainDF, test]], feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, verbose=0)
        # save results to lists of pandas DFs
        total_cv_dfs_lst.append(CV_all_pd_df)
        mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf["ratio_negative_to_positive"] = ratio_params
display(mean_cv_pddf)

In [0]:
mean_cv_pddf.loc[mean_cv_pddf['f1_score'].idxmax()]['ratio_negative_to_positive']

In [0]:
maxIter_options = [15]
regParam_options = [0.0025]
elasticNetParam_options = [0.1]
ratio_params = [1.4, 1.5, 1.6, 1.7, 1.8, 1.9, 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0, 3.1, 3.2, 3.3, 3.4, 3.5]

# instantiate lists for collecting pandas dataframes
total_cv_dfs_lst = []
mean_cv_dfs_lst = []

for desired_neg_to_pos_ratio in ratio_params:
  negativeDF = trainAll.filter(trainAll['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
  positiveDF = trainAll.filter(trainAll['DEP_DEL15']==1)
  new_trainDF = positiveDF.union(negativeDF).cache()
  for maxIter_val in maxIter_options:
    for regParam_val in regParam_options:
      for elasticNetParam_val in elasticNetParam_options:
        # run the CV
        CV_all_pd_df, CV_mean_pd_df = runCV_LogReg([[new_trainDF, test]], feature_list, maxIter_input=maxIter_val, regParam_input=regParam_val, elasticNetParam_input=elasticNetParam_val, verbose=0)
        # save results to lists of pandas DFs
        total_cv_dfs_lst.append(CV_all_pd_df)
        mean_cv_dfs_lst.append(CV_mean_pd_df)

# combine PD DFs into one
total_cv_pddf = pd.concat(total_cv_dfs_lst, ignore_index=True)
# display(total_cv_pddf)
mean_cv_pddf = pd.concat(mean_cv_dfs_lst, ignore_index=True)
mean_cv_pddf["ratio_negative_to_positive"] = ratio_params
display(mean_cv_pddf)

# (Appendix) Note for later weeks

In [0]:
results = predictions.select(['prediction', 'DEP_DEL15'])
results = results.withColumnRenamed('DEP_DEL15', 'true_value')

def evalPred(x):
  if x[0] == 1:
    if x[1] == 1:
      return 'TP'
    elif x[1] == 0:
      return 'FP'
  elif x[0] == 0:
    if x[1] == 1:
      return 'FN'
    elif x[1] == 0:
      return 'TN'

udf_evalPred = udf(lambda x:evalPred(x))
results_2 = results.withColumn("result", udf_evalPred(array('prediction','true_value')))
display(results_2)

display(results_2.groupby(['prediction','true_value','result']).count())